In [1]:
import PyPDF2
from PyPDF2 import PdfReader
import os

In [12]:
import json
from src.db_local_storage.files_db import VECTOR_FILES_DIRECTORY


with open(VECTOR_FILES_DIRECTORY, "r") as file:
    loaded_data = json.load(file)

In [32]:
for document in loaded_data.values():
  print(document["data"][0]["embedding"])

[-0.09148407727479935, -0.3296155333518982, 0.19553515315055847, -0.13005883991718292, -0.023037904873490334, -0.27768027782440186, -0.15001057088375092, 0.061617735773324966, -0.21048811078071594, -0.1158759668469429, 0.00262309773825109, -0.18505680561065674, -0.36614593863487244, 0.01263430155813694, -0.23454351723194122, 0.026990391314029694, 0.10782455652952194, 0.20590373873710632, 0.01619311049580574, -0.29646965861320496, -0.49789899587631226, -0.3155633509159088, 0.22015143930912018, -0.17993934452533722, -0.2728782892227173, -0.24151268601417542, -0.2213350087404251, -0.1546640843153, 0.18654145300388336, -0.3817594647407532, 0.27131369709968567, -0.16452756524085999, 0.4666154384613037, -0.23997938632965088, -0.16251197457313538, 0.45274969935417175, -0.06473690271377563, 0.030141692608594894, 0.18030805885791779, 0.3573063910007477, 0.057827189564704895, -0.5050416588783264, 0.14762045443058014, -0.24115344882011414, 0.12714245915412903, -0.30607476830482483, 0.036287162452

In [33]:
def organize_db(db):
  text_data = [] 
  embeddings = []

  for document in db.values():
    for page in document["data"]:
      text_data.append(page["metadata"]["original_text"])
      embeddings.append(page["embedding"])
  return text_data, embeddings

    

In [34]:
text_data, embeddings = organize_db(loaded_data)

In [44]:
text_data

['Dear Hiring Manager,\nI am writing to express my interest in the Machine Learning / AI Scientist position at Grazper.\nWith a strong background in human-centered artificial intelligence, hands-on experience in\ndeveloping machine learning models, and a deep passion for applying AI to solve real-world\nproblems, I am excited about the opportunity to contribute to Grazper’s innovative work in\nhuman pose estimation and behavioral analysis.\nMy role as Co-Founder of NeoCareU had provided me with extensive experience',
 ' in\ndeveloping Python-based infrastructures for graph search functionality, utilizing frameworks\nsuch as FastAPI and Uvicorn. I have led end-to-end development of features, improving user\nexperiences and backend processes with technologies like Node.js and TypeScript. This\nexperience has sharpened my software development skills and my ability to translate\ncomplex machine learning concepts into practical applications, a key requirement for the role\nat Grazper.\nIn a

In [41]:
def lexical_search(query: str, chunks: list) -> list:
        return [chunk for chunk in chunks if query.lower() in chunk.lower()]

In [4]:
from transformers import pipeline

qa_pipeline = pipeline(
            "question-answering", model="deepset/roberta-base-squad2"
        )

query = "What is the capital of Germany?"
context = "The capital of Germany is Paris"
response = qa_pipeline(question=query, context=context)

In [6]:
{"message": response['answer'], "context_used": context, "chunks": context}


{'message': 'Paris',
 'context_used': 'The capital of Germany is Paris',
 'chunks': 'The capital of Germany is Paris'}

In [48]:
from typing import List
import numpy as np

def semantic_search(query: str, chunks: List[str], embeddings: np.ndarray, model) -> List[str]:
    query_embedding = model.encode([query])
    similarities = np.dot(embeddings, query_embedding.T).flatten()
    top_indices = np.argsort(-similarities)[:3]  # Get top 3 results
    return [chunks[i] for i in top_indices]

In [47]:
lexical_search("ware", text_data)

[' in\ndeveloping Python-based infrastructures for graph search functionality, utilizing frameworks\nsuch as FastAPI and Uvicorn. I have led end-to-end development of features, improving user\nexperiences and backend processes with technologies like Node.js and TypeScript. This\nexperience has sharpened my software development skills and my ability to translate\ncomplex machine learning concepts into practical applications, a key requirement for the role\nat Grazper.\nIn addition to my professional experience, I hol',
 'ftware development to Grazper and to help drive the continued\ninnovation that the company is known for. I look forward to the possibility of discussing how\nmy background, skills, and experiences align with the needs of your team.\nSincerely,']

In [4]:
# file_path = "/home/alexabades/DocuRAG/Api/src/db_local_storage/files/doc_test.pdf"
file_path = "/home/alexabades/DocuRAG/Api/doc_test.pdf"

print(os.path.exists(file_path))
print(os.access(file_path, os.R_OK))

with open(file_path, "rb") as pdf_file:
    reader = PdfReader(pdf_file)
    text = ""
    for page in reader.pages:
        text += page.extract_text()

True
True


In [12]:
import pdfplumber

# with pdfplumber.open(file_path) as pdf:
#     first_page = pdf.pages[0]
#     print(first_page.extract_text())

with pdfplumber.open(file_path) as pdf:
    text = ""
    for page in pdf.pages:
        text += page.extract_text()

In [11]:
def chunk_text(text, chunk_size=512):
    chunks = [text[i : i + chunk_size] for i in range(0, len(text), chunk_size)]
    return chunks

In [15]:
chunks = chunk_text(text)

In [17]:
from sentence_transformers import SentenceTransformer


model = SentenceTransformer("paraphrase-MiniLM-L6-v2")

embeddings = []
for chunk in chunks:
    embeddings.append(model.encode(chunk))
    print(chunk)
    break

/home/alexabades/DocuRAG/Api/venv/lib/python3.10/site-packages/sentence_transformers/cross_encoder/CrossEncoder.py:11: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from tqdm.autonotebook import tqdm, trange
/home/alexabades/DocuRAG/Api/venv/lib/python3.10/site-packages/torch/cuda/__init__.py:128: UserWarning: CUDA initialization: The NVIDIA driver on your system is too old (found version 11070). Please update your GPU driver by downloading and installing a new version from the URL: http://www.nvidia.com/Download/index.aspx Alternatively, go to: https://pytorch.org to install a PyTorch version that has been compiled with your version of the CUDA driver. (Triggered internally at ../c10/cuda/CUDAFunctions.cpp:108.)
  return torch._C._cuda_getDeviceCount() > 0
/home/alexabades/DocuRAG/Api/venv/lib/python3.10/site-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_toke

Dear Hiring Manager,
I am writing to express my interest in the Machine Learning / AI Scientist position at Grazper.
With a strong background in human-centered artificial intelligence, hands-on experience in
developing machine learning models, and a deep passion for applying AI to solve real-world
problems, I am excited about the opportunity to contribute to Grazper’s innovative work in
human pose estimation and behavioral analysis.
My role as Co-Founder of NeoCareU had provided me with extensive experience


In [19]:
path = "/home/alexabades/DocuRAG/Api/src/db_local_storage/vectorized_db/vectorized_data.json"

import json

with open(path, "r") as f:
    loaded_data = json.load(f)

In [24]:
loaded_data["emedding_data"]

{}

In [ ]:
pdf_reader = PyPDF2.PdfReader(io.BytesIO(pdf_file.file.read()))
text = ""
for page_num in range(pdf_reader.numPages):
    page = pdf_reader.getPage(page_num)
    text += page.extract_text()